## Assessment Center: Python Datenanalyse

Willkommen zu unserem Python Skill Assessment. In diesem Notebook werden Sie gebeten, eine Reihe von Datenanalyse-Aufgaben durchzuführen.

**Die Aufgabe:**
Wir analysieren die Datei `Lastgang.csv`, die Messdaten (Stromverbrauch, Temperatur etc.) im 15-Minuten-Takt für ein Universitätsgebäude enthält.

**Ihr Setup:**
Um Ihnen den Einstieg zu erleichtern, stellen wir Ihnen die ersten Zellen zur Verfügung. Diese laden die Daten, bereiten sie auf und führen eine erste Visualisierung sowie eine Datentransformation (Pivot-Tabellen) durch. Sie können diesen Code ausführen, um Ihre Arbeitsumgebung einzurichten.

**Ihre Aufgaben:**
Im Anschluss an die vorbereiteten Zellen finden Sie eine Liste von Aufgaben. Diese sind von Ihnen selbstständig zu lösen.

**Wichtiger Hinweis:** Die Anzahl der Aufgaben ist bewusst so gewählt, dass sie wahrscheinlich nicht alle in der zur Verfügung stehenden Zeit bewältigt werden können. **Das ist beabsichtigt.** Bitte bearbeiten Sie so viele Aufgaben, wie Sie schaffen. Konzentrieren Sie sich auf sauberen, lesbaren und korrekten Code.

**Hilfestellung:** Bitte verwenden Sie keine KI zur Codegenerierung, sie können jedoch ohne weiteres Internetrecherche verwenden um geeignete Bibliotheken oder Funktionen zu finden.

Viel Erfolg!

---
### 1: Datenimport und Vorbereitung

Im ersten Schritt importieren wir die `pandas`-Bibliothek. Anschließend lesen wir die Datei `Lastgang.csv` ein. Dabei achten wir auf die Besonderheiten der Datei:
* Trennzeichen ist ein Semikolon (`;`).
* Dezimaltrennzeichen ist ein Komma (`,`).
* Die Spalte `Datum` wird direkt als Datums-Objekt eingelesen (`parse_dates`) und als Index des DataFrames gesetzt.

Abschließend prüfen wir mit `df.head()` und `df.info()`, ob der Import erfolgreich war.

In [ ]:
import pandas as pd

df = pd.read_csv(
    'Lastgang.csv',
    sep=';',
    decimal=',',
    parse_dates=['Datum'],
    dayfirst=True
)

df = df.set_index('Datum')

df.head()

Stromverbrauch [kW]  Temperatur [°C]  \
Datum                                                       
2022-01-01 00:15:00                 1120            14.80   
2022-01-01 00:30:00                 1170            14.75   
2022-01-01 00:45:00                 1155            14.70   
2022-01-01 01:00:00                 1150            14.45   
2022-01-01 01:15:00                 1145            14.20   

                     Luftfeuchtigkeit [% r.F.]  Globalstrahlung [W/m²]  
Datum                                                                   
2022-01-01 00:15:00                       60.0                     0.0  
2022-01-01 00:30:00                       60.5                     0.0  
2022-01-01 00:45:00                       61.0                     0.0  
2022-01-01 01:00:00                       61.5                     0.0  
2022-01-01 01:15:00                       62.0                     0.0

### 2: Visualisierung der Zeitreihen

Da die vier Messgrößen sehr unterschiedliche Einheiten und Wertebereiche haben (kW, °C, %, W/m²), ist ein gemeinsamer Plot unübersichtlich.

Wir verwenden hier `plotly.subplots`, um vier separate Diagramme untereinander zu erstellen. Mit `shared_xaxes=True` stellen wir sicher, dass alle Plots dieselbe X-Achse (das Datum) verwenden, was den Vergleich erleichtert.

In [ ]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

columns_to_plot = [
    'Stromverbrauch [kW]',
    'Temperatur [°C]',
    'Luftfeuchtigkeit [% r.F.]',
    'Globalstrahlung [W/m²]'
]

fig = make_subplots(
    rows=len(columns_to_plot),
    cols=1,
    shared_xaxes=True,
    subplot_titles=columns_to_plot
)

for i, col_name in enumerate(columns_to_plot):

    fig.add_trace(
        go.Scatter(
            x=df.index,
            y=df[col_name],
            name=col_name
        ),
        row=i + 1,
        col=1
    )

fig.update_layout(
    height=1600,
    title_text='Zeitreihendaten',
    showlegend=False
)

fig.update_xaxes(title_text='Datum', row=len(columns_to_plot), col=1)

fig.show()

### 3: Pivot-Tabellen erstellen

Für viele Analysen (z.B. die Untersuchung von Tagesprofilen) ist es hilfreich, die Daten in einer Pivot-Form zu haben, bei der jede Zeile einen Tag und jede Spalte eine Uhrzeit darstellt.

Wir erstellen hierfür vier separate Pivot-Tabellen (für jede Messgröße eine). Die neuen, einfacheren Variablennamen (`stromverbrauch_pv`, `temperatur_pv` etc.) können Sie in den folgenden Aufgaben direkt verwenden.

In [ ]:
df_temp = df.reset_index()

df_temp['Tag'] = df_temp['Datum'].dt.date
df_temp['Uhrzeit'] = df_temp['Datum'].dt.time

stromverbrauch_pv = pd.pivot_table(
    df_temp,
    values='Stromverbrauch [kW]',
    index='Tag',
    columns='Uhrzeit',
    aggfunc='mean'
)

temperatur_pv = pd.pivot_table(
    df_temp,
    values='Temperatur [°C]',
    index='Tag',
    columns='Uhrzeit',
    aggfunc='mean'
)

luftfeuchtigkeit_pv = pd.pivot_table(
    df_temp,
    values='Luftfeuchtigkeit [% r.F.]',
    index='Tag',
    columns='Uhrzeit',
    aggfunc='mean'
)

globalstrahlung_pv = pd.pivot_table(
    df_temp,
    values='Globalstrahlung [W/m²]',
    index='Tag',
    columns='Uhrzeit',
    aggfunc='mean'
)


stromverbrauch_pv.head()


Uhrzeit     00:00:00  00:15:00  00:30:00  00:45:00  01:00:00  01:15:00  \
Tag                                                                      
2022-01-01       NaN    1120.0    1170.0    1155.0    1150.0    1145.0   
2022-01-02    1005.0    1045.0    1050.0    1050.0    1035.0    1045.0   
2022-01-03    1005.0    1010.0     995.0     995.0    1005.0    1005.0   
2022-01-04    1060.0    1065.0    1070.0    1080.0    1065.0    1060.0   
2022-01-05    1130.0    1125.0    1130.0    1110.0    1100.0    1125.0   

Uhrzeit     01:30:00  01:45:00  02:00:00  02:15:00  ...  21:30:00  21:45:00  \
Tag                                                 ...                       
2022-01-01    1140.0    1150.0    1145.0    1150.0  ...    1050.0    1050.0   
2022-01-02    1005.0    1030.0    1015.0    1020.0  ...    1000.0    1000.0   
2022-01-03     995.0     995.0    1005.0    1000.0  ...    1100.0    1095.0   
2022-01-04    1065.0    1065.0    1060.0    1055.0  ...    1140.0    1110.0   
2022-01-05    1120.0    1120.0    1135.0    1125.0  ...    1135.0    1130.0   

Uhrzeit     22:00:00  22:15:00  22:30:00  22:45:00  23:00:00  23:15:00  \
Tag                                                                      
2022-01-01    1010.0    1070.0    1020.0    1070.0    1000.0    1040.0   
2022-01-02    1015.0    1005.0     995.0     995.0    1005.0    1000.0   
2022-01-03    1090.0    1090.0    1090.0    1080.0    1070.0    1065.0   
2022-01-04    1095.0    1110.0    1120.0    1105.0    1100.0    1100.0   
2022-01-05    1130.0    1135.0    1130.0    1130.0    1125.0    1130.0   

Uhrzeit     23:30:00  23:45:00  
Tag                             
2022-01-01    1035.0    1065.0  
2022-01-02     995.0    1000.0  
2022-01-03    1070.0    1075.0  
2022-01-04    1120.0    1130.0  
2022-01-05    1130.0    1125.0  

[5 rows x 96 columns]

### Aufgabe 1: Geordnete Jahresdauerlinie erstellen
Erstellen Sie eine Grafik der geordneten Jahresdauerlinie. Diese soll alle Stromverbrauchswerte (kW) des Jahres, sortiert vom höchsten bis zum niedrigsten Wert, anzeigen.

In [ ]:
import plotly.express as px

# 1. Alle Stromverbrauchswerte absteigend sortieren


# 2. Dauerlinie plotten



### Aufgabe 2: Gesamtenergieverbrauch berechnen
Berechnen Sie den gesamten Energieverbrauch (in MWh) für den gesamten Zeitraum des Datensatzes.

In [ ]:
# 1. Summe aller Leistungswerte (kW)


# 2. Umrechnung in kWh


# 3. Umrechnung in MWh (kWh / 1000)


# 4. Gesamtverbrauch ausgeben


Gesamtenergieverbrauch: 11063.49 MWh


### Aufgabe 3: Monatsverbräuche berechnen und visualisieren
Berechnen Sie den monatlichen Gesamtenergieverbrauch (in MWh) und stellen Sie das Ergebnis in einem Balkendiagramm dar.

In [ ]:
import plotly.express as px

# 1. Energie (kWh) für jeden 15-Min-Takt berechnen

# 2. Nach Monat resampeln, summieren und in MWh umwandeln

# 3. Als Balkendiagramm plotten


/tmp/ipython-input-3648519741.py:8: FutureWarning:

'M' is deprecated and will be removed in a future version, please use 'ME' instead.



### Aufgabe 4: Durchschnittliche Tagesprofile (Mo-So) erstellen
Erstellen Sie ein Liniendiagramm, das das durchschnittliche Stromverbrauchsprofil über 24 Stunden zeigt. Es soll für jeden Wochentag (Montag bis Sonntag) eine eigene Linie geben.

In [ ]:
import plotly.express as px

# 1. Wochentag und Uhrzeit als neue Spalten hinzufügen
# (Falls nicht schon in einer vorherigen Zelle geschehen)


# 2. Nach Wochentag und Uhrzeit gruppieren und Mittelwert bilden


# 3. Sortiere erst nach Wochentag (Nr), DANN nach Uhrzeit

# 4. Profile plotten


### Aufgabe 5: Temperaturkorrelation darstellen (XY-Plot)
Erstellen Sie einen Scatter-Plot (XY-Plot), um den Zusammenhang zwischen dem Stromverbrauch (kW) und der Temperatur (°C) darzustellen.

In [ ]:
import plotly.express as px

# Scatter-Plot: Temperatur auf X-Achse, Stromverbrauch auf Y-Achse


### Aufgabe 6: Heatmap erstellen
Visualisieren Sie die `stromverbrauch_pv` Pivot-Tabelle als Heatmap. Die Achsen sollen die Tage des Jahres (horizontal) und die Uhrzeiten des Tages (vertikal) darstellen.

In [1]:
import plotly.express as px

# 1. Pivot-Tabelle transponieren (T), damit Uhrzeit (Index) vertikal ist

# 2. Heatmap mit der transponierten Tabelle erstellen


### Aufgabe 7: Spitzenlast berechnen
Ermitteln Sie die absolute Spitzenlast (den höchsten gemessenen Stromverbrauchswert in kW) im gesamten Datensatz und geben Sie an, zu welchem Zeitpunkt dieser Wert aufgetreten ist.

In [2]:
# 1. Höchsten Wert finden

# 2. Zeitpunkt (Index) des höchsten Werts finden


### Aufgabe 8: Grundlast berechnen
Berechnen Sie die Grundlast (in kW). Diese ist definiert als die Leistung, die an mindestens 7.500 Stunden pro Jahr anfällt (überschritten oder erreicht wird).

In [ ]:
# 1. Jahresdauerlinie erstellen (falls nicht schon in A1 geschehen)

# 2. Den Wert an der 7.500 Stunden in der geordneten Jahresdauerlinie ablesen


Die Grundlast (Leistung bei 7500h) beträgt: 1085 kW


### Aufgabe 9: Relativen Energieverbrauch der Grundlast berechnen
Berechnen Sie, welchen prozentualen Anteil der Energieverbrauch innerhalb des Grundlastbandes am Gesamtenergieverbrauch hat. Das Grundlastband wird durch die in A8 ermittelte Leistung (`grundlast_kw`) nach oben begrenzt.

**Hinweis**: Fläche in der geordneten Jahredauerlinie wo Leistung <= Grundlast